In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import random
import logging

from data_prep import Password as P
from model import Generator, Discriminator
from training_helper import *
from config import *

logger = logging.getLogger()
logger.setLevel(logging.DEBUG)

In [2]:
# custom weights initialization called on G and D
def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Linear') != -1:
        nn.init.normal_(m.weight.data, 0, 0.001)

In [3]:
def get_train_dis(strings_in, pred, seq_len):
    real, real_sub = get_real(strings_in, seq_len)
    fake = get_fake(real, pred, seq_len)
    return real_sub, fake

def get_train_gen(strings_in, pred, seq_len):
    real, _ = get_real(strings_in, seq_len)
    fake = get_fake(real, pred, seq_len)
    return fake

def get_fake(real, pred, seq_len):
    train_pred = torch.zeros(0, seq_len+1, CHARMAP_LEN).to(device)
    real = real.to(torch.float)
    for i in range(1, seq_len+1):
        train_pred = torch.cat((
            train_pred,
            torch.cat((
                torch.zeros(BATCH_SIZE, seq_len-i, CHARMAP_LEN).to(device),
                real[:,:i,:],
                pred[:,i-1:i,:]
                ),dim = 1)
            ),dim = 0)
    return train_pred

def get_real(strings_in, seq_len):
    real = torch.LongTensor(BATCH_SIZE, seq_len+1, CHARMAP_LEN).zero_().to(device)
    real_sub = torch.FloatTensor(0, seq_len+1, CHARMAP_LEN).zero_().to(device)
    for i in range(BATCH_SIZE):
        # l = len(strings_in[i]) if len(strings_in[i]) <= seq_len else seq_len
        if len(strings_in[i]) <= seq_len:
            l = len(strings_in[i])
            real[i][l][CHARMAP_LEN - 1] = 1
        else:
            l = seq_len
        for j in range(l):
            real[i][j][P.letterToIndex(strings_in[i][j])] = 1
        
    for i in range(1, seq_len+1):
        real_sub = torch.cat((
            real_sub,
            torch.cat((
                torch.zeros(BATCH_SIZE, seq_len-i, CHARMAP_LEN).to(device),
                real[:,:i+1,:].to(torch.float)
            ), dim = 1)
        ), dim = 0)
    return real, real_sub

def get_interpolate(real, fake):
    real = torch.autograd.Variable(real.data).data
    fake = torch.autograd.Variable(fake.data).data
    alpha = torch.rand(real.size()[0], 1, 1).to(device)
    alpha = alpha.expand(real.size())
    return torch.autograd.Variable(alpha * real + (1 - alpha) * fake).data

In [4]:
g = Generator(GEN_HIDDEN_SIZE, GEN_NEURON_SIZE).to(device)
d = Discriminator(DISC_HIDDEN_SIZE, DISC_NEURON_SIZE).to(device)

In [5]:
#opt_g = torch.optim.Adam(g.parameters(), lr=0.0002, betas=(0.5, 0.999))
#opt_d = torch.optim.Adam(d.parameters(), lr=0.0002, betas=(0.5, 0.999))
opt_g = torch.optim.RMSprop(g.parameters(), lr=0.0002)
opt_d = torch.optim.RMSprop(d.parameters(), lr=0.0002)

In [6]:
p = P()
batch_gen = p.string_gen

INFO:root:Initializing passwords...
DEBUG:root:Loading from existing json file...
INFO:root:Done initializing passwords.


In [8]:
print_every = 100
loss_trend = []
logging.info("---------- Pre-training generator ----------")
for i in range(PRE_GEN_ITERS):
    pas = next(batch_gen)
    input_tensor = P.passwordToInputTensor(pas).to(device)
    target_tensor = P.passwordToTargetTensor(pas).to(device)
    output, loss = g.pre_train(input_tensor, target_tensor)
    
    if i % print_every == 0:
        loss_trend.append(loss)
        logging.debug("Iter: "+ str(i)+" Loss: "+str(loss))

INFO:root:---------- Pre-training generator ----------


TypeError: forward() missing 1 required positional argument: 'seq_len'

In [ ]:
logger.setLevel(logging.DEBUG)

for seq_len in range(MIN_LEN, MAX_LEN + 1):
    logging.info("---------- Adversarial Training with seq_len %d ----------\n" % (seq_len))

    for i in range(1, ADVERSIVE_ITERS + 1):
        logging.debug("----------------- %d / %d -----------------" % (i, ADVERSIVE_ITERS))
        logging.debug("Training discriminator...")

        d.requiresGrad()
        d.zero_grad()
        g.zero_grad()
        for j in range(CRITIC_ITERS):
            with torch.backends.cudnn.flags(enabled=False):
                L = 0

                data = next(batch_gen)
                pred = g(data, seq_len)
                real, fake = get_train_dis(data, pred, seq_len)
                interpolate = get_interpolate(real, fake)

                # Genuine
                disc_real = d(real, seq_len)
                loss_real = -disc_real.mean()
                logging.debug("real loss: "+str(loss_real.item()))
                L += loss_real

                # Fake
                disc_fake = d(fake, seq_len)
                loss_fake = disc_fake.mean()
                logging.debug("fake loss: "+str(loss_fake.item()))
                L += loss_fake

                # Gradient penalty
                interpolate = torch.autograd.Variable(interpolate, requires_grad=True)
                disc_interpolate = d(interpolate, seq_len)
                grad = torch.ones_like(disc_interpolate).to(device)
                gradients = torch.autograd.grad(
                        outputs=disc_interpolate,
                        inputs=interpolate,
                        grad_outputs=grad,
                        create_graph=True,
                        retain_graph=True,
                        only_inputs=True,
                    )[0]
                loss_gp = ((gradients.norm(2, dim=2) - 1) ** 2).mean() * LAMBDA
                logging.debug("grad loss: "+str(loss_gp.item()))
                L += loss_gp

                L.backward(retain_graph=False)
                opt_d.step()


        logging.debug("Done. Classification accuracy: " + "???" + " Loss: " + str(L.item()))    

        logging.debug("Training generator...")

        d.requiresNoGrad()

        for j in range(GEN_ITERS):
            data = next(batch_gen)
            pred = g(data, seq_len)
            fake = get_train_gen(data, pred, seq_len)
            loss_gen = -d(fake, seq_len).mean()
            logging.debug("gen iter: " + str(j+1) + " loss: "+str(loss_gen.item()))
            loss_gen.backward(retain_graph=False)
            opt_g.step()

        logging.debug("Done training generator.\n")
        
    print(g.generate_N(p))
    

INFO:root:---------- Adversarial Training with seq_len 4 ----------

DEBUG:root:----------------- 1 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -0.04840271547436714
DEBUG:root:fake loss: 0.155635803937912
DEBUG:root:grad loss: 9.158235549926758
DEBUG:root:Done. Classification accuracy: ??? Loss: 9.26546859741211
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 5.423308372497559
DEBUG:root:gen iter: 2 loss: 5.421012878417969
DEBUG:root:Done training generator.

DEBUG:root:----------------- 2 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -0.2421589344739914
DEBUG:root:fake loss: -5.23301887512207
DEBUG:root:grad loss: 7.140565872192383
DEBUG:root:Done. Classification accuracy: ??? Loss: 1.6653881072998047
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 7.491553783416748
DEBUG:root:gen iter: 2 loss: 7.443231582641602
DEBUG:root:Done training generator.

DEBUG:root:----------------- 3 /

DEBUG:root:Done training generator.

DEBUG:root:----------------- 19 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -17.523521423339844
DEBUG:root:fake loss: -17.515785217285156
DEBUG:root:grad loss: 2.4460878372192383
DEBUG:root:Done. Classification accuracy: ??? Loss: -32.59321975708008
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 16.518356323242188
DEBUG:root:gen iter: 2 loss: 16.41731071472168
DEBUG:root:Done training generator.

DEBUG:root:----------------- 20 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -18.469512939453125
DEBUG:root:fake loss: -16.37181854248047
DEBUG:root:grad loss: 1.8998461961746216
DEBUG:root:Done. Classification accuracy: ??? Loss: -32.94148635864258
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 18.39862632751465
DEBUG:root:gen iter: 2 loss: 18.398298263549805
DEBUG:root:Done training generator.

DEBUG:root:----------------- 21 / 1000 ---------------

DEBUG:root:----------------- 37 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -22.63771629333496
DEBUG:root:fake loss: -22.42449188232422
DEBUG:root:grad loss: 2.4650940895080566
DEBUG:root:Done. Classification accuracy: ??? Loss: -42.59711456298828
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 21.871665954589844
DEBUG:root:gen iter: 2 loss: 21.804264068603516
DEBUG:root:Done training generator.

DEBUG:root:----------------- 38 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -23.226696014404297
DEBUG:root:fake loss: -21.823253631591797
DEBUG:root:grad loss: 1.2715225219726562
DEBUG:root:Done. Classification accuracy: ??? Loss: -43.77842712402344
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 22.635536193847656
DEBUG:root:gen iter: 2 loss: 22.616313934326172
DEBUG:root:Done training generator.

DEBUG:root:----------------- 39 / 1000 -----------------
DEBUG:root:Training discriminator

DEBUG:root:Training discriminator...
DEBUG:root:real loss: -26.464609146118164
DEBUG:root:fake loss: -25.442180633544922
DEBUG:root:grad loss: 1.4470065832138062
DEBUG:root:Done. Classification accuracy: ??? Loss: -50.45978546142578
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 25.557491302490234
DEBUG:root:gen iter: 2 loss: 25.57461166381836
DEBUG:root:Done training generator.

DEBUG:root:----------------- 56 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -26.56093406677246
DEBUG:root:fake loss: -25.539791107177734
DEBUG:root:grad loss: 1.3211166858673096
DEBUG:root:Done. Classification accuracy: ??? Loss: -50.779605865478516
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 25.7048282623291
DEBUG:root:gen iter: 2 loss: 25.67694664001465
DEBUG:root:Done training generator.

DEBUG:root:----------------- 57 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -26.79648208618164
DEBUG:root:fak

DEBUG:root:real loss: -29.404584884643555
DEBUG:root:fake loss: -28.195953369140625
DEBUG:root:grad loss: 1.4449102878570557
DEBUG:root:Done. Classification accuracy: ??? Loss: -56.1556282043457
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 28.116336822509766
DEBUG:root:gen iter: 2 loss: 28.131912231445312
DEBUG:root:Done training generator.

DEBUG:root:----------------- 74 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -29.52867889404297
DEBUG:root:fake loss: -28.110187530517578
DEBUG:root:grad loss: 1.1485662460327148
DEBUG:root:Done. Classification accuracy: ??? Loss: -56.490299224853516
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 28.775482177734375
DEBUG:root:gen iter: 2 loss: 28.796865463256836
DEBUG:root:Done training generator.

DEBUG:root:----------------- 75 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -29.449962615966797
DEBUG:root:fake loss: -28.801393508911133
DEBUG

...

DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 378.2189025878906
DEBUG:root:gen iter: 2 loss: 137.68470764160156
DEBUG:root:Done training generator.

DEBUG:root:----------------- 220 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -583.4479370117188
DEBUG:root:fake loss: -217.83465576171875
DEBUG:root:grad loss: 367.4273681640625
DEBUG:root:Done. Classification accuracy: ??? Loss: -433.855224609375
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 204.85572814941406
DEBUG:root:gen iter: 2 loss: 518.2681884765625
DEBUG:root:Done training generator.

DEBUG:root:----------------- 221 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -578.6405029296875
DEBUG:root:fake loss: -204.86460876464844
DEBUG:root:grad loss: 359.66558837890625
DEBUG:root:Done. Classification accuracy: ??? Loss: -423.83953857421875
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 135.7926788330078
DEBUG:root:

DEBUG:root:gen iter: 2 loss: 284.7643737792969
DEBUG:root:Done training generator.

DEBUG:root:----------------- 238 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -578.9654541015625
DEBUG:root:fake loss: -206.27149963378906
DEBUG:root:grad loss: 357.2883605957031
DEBUG:root:Done. Classification accuracy: ??? Loss: -427.9485778808594
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 212.19601440429688
DEBUG:root:gen iter: 2 loss: 212.14419555664062
DEBUG:root:Done training generator.

DEBUG:root:----------------- 239 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -575.4353637695312
DEBUG:root:fake loss: -290.85284423828125
DEBUG:root:grad loss: 395.6556396484375
DEBUG:root:Done. Classification accuracy: ??? Loss: -470.632568359375
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 206.22706604003906
DEBUG:root:gen iter: 2 loss: 206.13414001464844
DEBUG:root:Done training generator.

DEBUG:r

DEBUG:root:----------------- 256 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -573.2021484375
DEBUG:root:fake loss: -550.2357788085938
DEBUG:root:grad loss: 521.3338012695312
DEBUG:root:Done. Classification accuracy: ??? Loss: -602.1041870117188
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 547.4274291992188
DEBUG:root:gen iter: 2 loss: 467.3388671875
DEBUG:root:Done training generator.

DEBUG:root:----------------- 257 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -571.5133056640625
DEBUG:root:fake loss: -467.2602844238281
DEBUG:root:grad loss: 474.8022155761719
DEBUG:root:Done. Classification accuracy: ??? Loss: -563.9713134765625
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 46.68254089355469
DEBUG:root:gen iter: 2 loss: 125.74723052978516
DEBUG:root:Done training generator.

DEBUG:root:----------------- 258 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:

DEBUG:root:Training discriminator...
DEBUG:root:real loss: -584.8463134765625
DEBUG:root:fake loss: -203.52980041503906
DEBUG:root:grad loss: 350.72515869140625
DEBUG:root:Done. Classification accuracy: ??? Loss: -437.65093994140625
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 124.92971801757812
DEBUG:root:gen iter: 2 loss: 440.97247314453125
DEBUG:root:Done training generator.

DEBUG:root:----------------- 275 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -585.9218139648438
DEBUG:root:fake loss: -124.93936920166016
DEBUG:root:grad loss: 312.4122314453125
DEBUG:root:Done. Classification accuracy: ??? Loss: -398.448974609375
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 286.3969421386719
DEBUG:root:gen iter: 2 loss: 127.56304931640625
DEBUG:root:Done training generator.

DEBUG:root:----------------- 276 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -587.1597900390625
DEBUG:root:f

DEBUG:root:fake loss: -125.32190704345703
DEBUG:root:grad loss: 315.7658386230469
DEBUG:root:Done. Classification accuracy: ??? Loss: -390.7765808105469
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 43.44084548950195
DEBUG:root:gen iter: 2 loss: 200.19549560546875
DEBUG:root:Done training generator.

DEBUG:root:----------------- 293 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -583.1337280273438
DEBUG:root:fake loss: -200.22695922851562
DEBUG:root:grad loss: 344.547607421875
DEBUG:root:Done. Classification accuracy: ??? Loss: -438.8131103515625
DEBUG:root:Training generator...
DEBUG:root:gen iter: 1 loss: 439.8875732421875
DEBUG:root:gen iter: 2 loss: 202.67623901367188
DEBUG:root:Done training generator.

DEBUG:root:----------------- 294 / 1000 -----------------
DEBUG:root:Training discriminator...
DEBUG:root:real loss: -587.4280395507812
DEBUG:root:fake loss: -360.87359619140625
DEBUG:root:grad loss: 431.5640869140625
DEBUG:root:

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker

%matplotlib inline

logger.setLevel(logging.INFO)

plt.figure()
plt.plot(loss_trend)
#plt.savefig('pictures/rnn-rnn-loss.png',dpi=400)
plt.show()

In [ ]:
m = nn.LogSoftmax(dim=1)
loss = nn.NLLLoss()
# input is of size N x C = 3 x 5
input = torch.randn(3, 5, requires_grad=True)
# each element in target has to have 0 <= value < C
target = torch.tensor([1, 0, 4])
output = loss(m(input), target)

In [ ]:
import torch
a = torch.ones(3,2)
a.requires_grad = True
b = a * 2
ones = torch.ones_like(a)
g = torch.autograd.grad(
            outputs=b,
            inputs=a,
            grad_outputs=ones,
            create_graph=True,
            retain_graph=True,
            only_inputs=True,
        )

In [18]:
gr = nn.GRU(5, 6, 1, batch_first = True, dropout = 0).to(device)
inp = torch.ones(2,3,5).to(device)
print(inp.dim())
le = [2,3]
inp = nn.utils.rnn.pack_padded_sequence(inp, le, batch_first=True, enforce_sorted=False)
ii, batch_sizes, sorted_indices, unsorted_indices = inp
output = gr(inp)
batch_sizes, ii.dim()

3


(tensor([2, 2, 1]), 2)

In [15]:
output

(PackedSequence(data=tensor([[ 0.0091,  0.2609, -0.1818,  0.1562,  0.4007, -0.3006],
         [ 0.0091,  0.2609, -0.1818,  0.1562,  0.4007, -0.3006],
         [ 0.0104,  0.3125, -0.2223,  0.1676,  0.6060, -0.4805],
         [ 0.0104,  0.3125, -0.2223,  0.1676,  0.6060, -0.4805],
         [ 0.0116,  0.3035, -0.2305,  0.1259,  0.6981, -0.5952]],
        device='cuda:0', grad_fn=<CudnnRnnBackward>), batch_sizes=tensor([2, 2, 1]), sorted_indices=tensor([1, 0], device='cuda:0'), unsorted_indices=tensor([1, 0], device='cuda:0')),
 tensor([[[ 0.0104,  0.3125, -0.2223,  0.1676,  0.6060, -0.4805],
          [ 0.0116,  0.3035, -0.2305,  0.1259,  0.6981, -0.5952]]],
        device='cuda:0', grad_fn=<IndexSelectBackward>))

In [7]:
a = torch.ones(2,2,2).to('cuda')
a.requires_grad = True
gru = nn.GRU(2, 2, 1, batch_first = True, dropout = 0).to('cuda')
out, _ = gru(a)
grad = torch.ones_like(out).to('cuda')
gradients = torch.autograd.grad(
                outputs=out,
                inputs=a,
                grad_outputs=grad,
                create_graph=True,
                retain_graph=True,
                only_inputs=True,)[0]
loss_gp = ((gradients.norm(2, dim=2) - 1) ** 2).mean() * LAMBDA
print(loss_gp)
loss_gp.backward()

tensor(8.1020, device='cuda:0', grad_fn=<MulBackward0>)


RuntimeError: derivative for _cudnn_rnn_backward is not implemented

In [7]:
print(g.state_dict)

<bound method Module.state_dict of Generator(
  (embedding): Embedding(80, 1024)
  (gru): GRU(1024, 1024, batch_first=True)
  (h2o): Linear(in_features=1024, out_features=80, bias=True)
)>
